## Notebook to create a map with PDBe-KB/FunPDBe partners

In [1]:
### Uncomment to install packages
#!pip install folium
#!pip install bs4
#!pip install geocoder

In [2]:
import folium
from folium import plugins
from folium.features import CustomIcon
import requests
import pandas as pd
import bs4
import geocoder
import time
import json

#### Get the list of current partners from the PDBe-KB/FunPDBe website

In [3]:
def get_pdbekb_partners(url="https://www.ebi.ac.uk/pdbe/funpdbe/deposition"):
    text = requests.get(url).text
    soup = bs4.BeautifulSoup(text,"html.parser").find_all("div", attrs={"id": "partners"})[0].find_all("tr")
    values = []
    
    for ingredient in soup:
        values.append([x.get_text().strip() for x in ingredient.find_all("td")])
    
    return pd.DataFrame(columns=["Resource","PI","URL"], data=values)

In [4]:
partners = get_pdbekb_partners()
partners["PI"] = [x[:-6] for x in partners["PI"]]
partners

Resource                                PI  \
0     14-3-3-Pred                      Geoff Barton   
1      3D Complex                     Emmanuel Levy   
2    3DLigandSite                         Mark Wass   
3            AKID          Manuela Helmer Citterich   
4        Arpeggio                      Tom Blundell   
5        CamKinet                       Toby Gibson   
6          canSAR                Bissan Al-Lazikani   
7   CATH-FunSites                  Christine Orengo   
8      ChannelsDB                     Jaroslav Koca   
9     COSPI-Depth                  M.S. Madhusudhan   
10       DynaMine                       Wim Vranken   
11          FoldX                      Luis Serrano   
12          M-CSA                    Janet Thornton   
13       MetalPDB  Claudia Andreini, Antonio Rosato   
14     Missense3D                 Michael Sternberg   
15         P2Rank                      David Hoksza   
16       POPSCOMP                 Franca Fraternali   
17        ProKinO                  Natarajan Kannan   
18         SKEMPI                       Iain H Moal   

                                                  URL  
0            http://www.compbio.dundee.ac.uk/1433pred  
1   https://shmoo.weizmann.ac.il/elevy/3dcomplexV6...  
2          http://www.sbg.bio.ic.ac.uk/~3dligandsite/  
3                        http://akid.bio.uniroma2.it/  
4           http://biosig.unimelb.edu.au/arpeggioweb/  
5                    http://camkinet.embl.de/v2/home/  
6                           https://cansar.icr.ac.uk/  
7                             http://www.cathdb.info/  
8                     http://ncbr.muni.cz/ChannelsDB/  
9                  http://cospi.iiserpune.ac.in/depth  
10                       http://dynamine.ibsquare.be/  
11                          http://foldxsuite.crg.eu/  
12          https://www.ebi.ac.uk/thornton-srv/m-csa/  
13                     http://metalweb.cerm.unifi.it/  
14           http://www.sbg.bio.ic.ac.uk/~missense3d/  
15                                http://prankweb.cz/  
16                          http://popscomp.org:3838/  
17     http://vulcan.cs.uga.edu/prokino/about/prokino  
18                   https://life.bsc.es/pid/skempi2/

#### Add locations to each resource
Ideally, this could be included on the website, but no biggie

In [5]:
city_dict = {
    '14-3-3-Pred': ['Dundee, UK'], 
    '3D Complex': ['Rehovot, Israel'], 
    '3DLigandSite': ['Canterbury, UK'], 
    'AKID': ['Rome, Italy'], 
    'Arpeggio': ['Cambridge, UK'], 
    'CamKinet': ['Heidelberg, Germany'], 
    'canSAR': ['Sutton, UK'], 
    'CATH-FunSites': ['London, UK'], 
    'ChannelsDB': ['Brno, Czech Republic'], 
    'COSPI-Depth': ['Pune, India'], 
    'DynaMine': ['Brussels, Belgium'], 
    'FoldX': ['Barcelona, Spain'], 
    'M-CSA': ['Hinxton, UK'], 
    'MetalPDB': ['Florence, Italy'], 
    'Missense3D': ['London, UK'], 
    'P2Rank': ['Prague, Czech Republic'], 
    'POPSCOMP': ['London, UK'], 
    'ProKinO': ['Athens, GA, USA'], 
    'SKEMPI': ['Barcelona, Spain']
}

In [6]:
partners.set_index("Resource", inplace=True)
locations = pd.DataFrame(data=city_dict).T
locations.columns=["Location"]
partners = partners.join(locations)
partners

PI  \
Resource                                          
14-3-3-Pred                        Geoff Barton   
3D Complex                        Emmanuel Levy   
3DLigandSite                          Mark Wass   
AKID                   Manuela Helmer Citterich   
Arpeggio                           Tom Blundell   
CamKinet                            Toby Gibson   
canSAR                       Bissan Al-Lazikani   
CATH-FunSites                  Christine Orengo   
ChannelsDB                        Jaroslav Koca   
COSPI-Depth                    M.S. Madhusudhan   
DynaMine                            Wim Vranken   
FoldX                              Luis Serrano   
M-CSA                            Janet Thornton   
MetalPDB       Claudia Andreini, Antonio Rosato   
Missense3D                    Michael Sternberg   
P2Rank                             David Hoksza   
POPSCOMP                      Franca Fraternali   
ProKinO                        Natarajan Kannan   
SKEMPI                              Iain H Moal   

                                                             URL  \
Resource                                                           
14-3-3-Pred             http://www.compbio.dundee.ac.uk/1433pred   
3D Complex     https://shmoo.weizmann.ac.il/elevy/3dcomplexV6...   
3DLigandSite          http://www.sbg.bio.ic.ac.uk/~3dligandsite/   
AKID                                http://akid.bio.uniroma2.it/   
Arpeggio               http://biosig.unimelb.edu.au/arpeggioweb/   
CamKinet                        http://camkinet.embl.de/v2/home/   
canSAR                                 https://cansar.icr.ac.uk/   
CATH-FunSites                            http://www.cathdb.info/   
ChannelsDB                       http://ncbr.muni.cz/ChannelsDB/   
COSPI-Depth                   http://cospi.iiserpune.ac.in/depth   
DynaMine                            http://dynamine.ibsquare.be/   
FoldX                                  http://foldxsuite.crg.eu/   
M-CSA                  https://www.ebi.ac.uk/thornton-srv/m-csa/   
MetalPDB                          http://metalweb.cerm.unifi.it/   
Missense3D              http://www.sbg.bio.ic.ac.uk/~missense3d/   
P2Rank                                       http://prankweb.cz/   
POPSCOMP                               http://popscomp.org:3838/   
ProKinO           http://vulcan.cs.uga.edu/prokino/about/prokino   
SKEMPI                          https://life.bsc.es/pid/skempi2/   

                             Location  
Resource                               
14-3-3-Pred                Dundee, UK  
3D Complex            Rehovot, Israel  
3DLigandSite           Canterbury, UK  
AKID                      Rome, Italy  
Arpeggio                Cambridge, UK  
CamKinet          Heidelberg, Germany  
canSAR                     Sutton, UK  
CATH-FunSites              London, UK  
ChannelsDB       Brno, Czech Republic  
COSPI-Depth               Pune, India  
DynaMine            Brussels, Belgium  
FoldX                Barcelona, Spain  
M-CSA                     Hinxton, UK  
MetalPDB              Florence, Italy  
Missense3D                 London, UK  
P2Rank         Prague, Czech Republic  
POPSCOMP                   London, UK  
ProKinO               Athens, GA, USA  
SKEMPI               Barcelona, Spain

#### Get geolocation data for each resource
The geocoding data provider (OpenStreetMaps) has a strict limit of no more than 1 request per second. 

In [7]:
def get_lat_lng(locality):
    g = geocoder.osm(locality).json
    return (g["lat"], g["lng"])

In [8]:
latitudes = []
longitudes = []

for locality in partners["Location"]:
    lat, lng = get_lat_lng(locality)
    latitudes.append(lat)
    longitudes.append(lng)
    time.sleep(1)

#### Add geolocation data to the dataframe
Also add country as a separate column, and replace abbreviations with the full name of the country

In [9]:
partners["Latitude"] = latitudes
partners["Longitude"] = longitudes
partners["Country"] = [x.split(", ")[-1] for x in partners["Location"]]
partners.replace(to_replace="UK", value="United Kingdom", inplace=True)
partners.replace(to_replace="USA", value="United States of America", inplace=True)
partners

PI  \
Resource                                          
14-3-3-Pred                        Geoff Barton   
3D Complex                        Emmanuel Levy   
3DLigandSite                          Mark Wass   
AKID                   Manuela Helmer Citterich   
Arpeggio                           Tom Blundell   
CamKinet                            Toby Gibson   
canSAR                       Bissan Al-Lazikani   
CATH-FunSites                  Christine Orengo   
ChannelsDB                        Jaroslav Koca   
COSPI-Depth                    M.S. Madhusudhan   
DynaMine                            Wim Vranken   
FoldX                              Luis Serrano   
M-CSA                            Janet Thornton   
MetalPDB       Claudia Andreini, Antonio Rosato   
Missense3D                    Michael Sternberg   
P2Rank                             David Hoksza   
POPSCOMP                      Franca Fraternali   
ProKinO                        Natarajan Kannan   
SKEMPI                              Iain H Moal   

                                                             URL  \
Resource                                                           
14-3-3-Pred             http://www.compbio.dundee.ac.uk/1433pred   
3D Complex     https://shmoo.weizmann.ac.il/elevy/3dcomplexV6...   
3DLigandSite          http://www.sbg.bio.ic.ac.uk/~3dligandsite/   
AKID                                http://akid.bio.uniroma2.it/   
Arpeggio               http://biosig.unimelb.edu.au/arpeggioweb/   
CamKinet                        http://camkinet.embl.de/v2/home/   
canSAR                                 https://cansar.icr.ac.uk/   
CATH-FunSites                            http://www.cathdb.info/   
ChannelsDB                       http://ncbr.muni.cz/ChannelsDB/   
COSPI-Depth                   http://cospi.iiserpune.ac.in/depth   
DynaMine                            http://dynamine.ibsquare.be/   
FoldX                                  http://foldxsuite.crg.eu/   
M-CSA                  https://www.ebi.ac.uk/thornton-srv/m-csa/   
MetalPDB                          http://metalweb.cerm.unifi.it/   
Missense3D              http://www.sbg.bio.ic.ac.uk/~missense3d/   
P2Rank                                       http://prankweb.cz/   
POPSCOMP                               http://popscomp.org:3838/   
ProKinO           http://vulcan.cs.uga.edu/prokino/about/prokino   
SKEMPI                          https://life.bsc.es/pid/skempi2/   

                             Location   Latitude  Longitude  \
Resource                                                      
14-3-3-Pred                Dundee, UK  56.460594  -2.970190   
3D Complex            Rehovot, Israel  31.895253  34.810562   
3DLigandSite           Canterbury, UK  51.280028   1.080253   
AKID                      Rome, Italy  41.893320  12.482932   
Arpeggio                Cambridge, UK  52.203482   0.123582   
CamKinet          Heidelberg, Germany  49.409358   8.694724   
canSAR                     Sutton, UK  51.357511  -0.173640   
CATH-FunSites              London, UK  51.507322  -0.127647   
ChannelsDB       Brno, Czech Republic  49.192244  16.611338   
COSPI-Depth               Pune, India  18.521428  73.854454   
DynaMine            Brussels, Belgium  50.843671   4.367437   
FoldX                Barcelona, Spain  41.382894   2.177432   
M-CSA                     Hinxton, UK  52.084869   0.179261   
MetalPDB              Florence, Italy  43.769871  11.255576   
Missense3D                 London, UK  51.507322  -0.127647   
P2Rank         Prague, Czech Republic  50.087465  14.421254   
POPSCOMP                   London, UK  51.507322  -0.127647   
ProKinO               Athens, GA, USA  33.959768 -83.376398   
SKEMPI               Barcelona, Spain  41.382894   2.177432   

                                Country  
Resource                                 
14-3-3-Pred              United Kingdom  
3D Complex                       Israel  
3DLigandSite             United Kingdom  
AKID      

#### The countries.geojson file is downloaded from https://datahub.io/core/geo-countries
This file is licensed under the "Open Data Commons Public Domain Dedication and License", while the original data comes from http://www.naturalearthdata.com/, a public domain dataset.
Essentially, it contains polygons describing country outlines.

In [10]:
countries_file = "https://datahub.io/core/geo-countries/r/countries.geojson"

countries_geo = requests.get(countries_file).json()    

#### Actual map plotting

In [14]:
# Base map. The tiles parameter defines how it looks like. Good options for this use case in my view are:
# "cartodbpositron", "Stamen watercolor", "Stamen toner". More options on the Folium documentation:
# https://python-visualization.github.io/folium/quickstart.html

pdbekb_map = folium.Map(location=[40, -5], zoom_start=2.5, tiles='cartodbpositron')

# Some utility styles, which can be as fancy as you like, really
# The colour codes used below are from http://colorbrewer2.org
# I copied them here purely for ease of access
# greens: ['#e5f5e0','#a1d99b','#31a354']
# blues: ['#deebf7','#9ecae1','#3182bd']

style_grey = lambda x: {
    'fillColor': '#cccccc',
    'color': "#aaaaaa"
}
style_green = lambda x: {
    'fillColor': '#e5f5e0',
    'color': "#a1d99b"
}
style_blue = lambda x: {
    'fillColor': '#deebf7',
    'color': "#9ecae1"
}

# Go over the countries of the world and check if PDBe-KB has partners in them
# Add their outlines to the map, skip others
for feature in countries_geo['features']:  
    if feature["properties"]["ADMIN"] in partners["Country"].values:
        folium.GeoJson(
            feature,
            style_function=style_green,
            name='geojson'
        ).add_to(pdbekb_map)    

# Create a cluster of markers for ech country. This looks better than each marker separately at low zoom
# At high zoom, the clusters split into individual labels
marker_clusters = {}
for country in set(partners.Country.values):
    marker_clusters[country] = plugins.MarkerCluster().add_to(pdbekb_map)

# Create markers and labels and add them to the cluster for the correct country
# They can also be aded to the map directly, but then will not be aggregated
for lat, lng, resource, url, country in zip(partners.Latitude, 
                                            partners.Longitude, 
                                            partners.index, 
                                            partners.URL,
                                            partners.Country
                                           ):
    label = f"<a href={url} target=_blank>{resource}</a>"
    # due to a bug in Folium, an icon must be defined each time it is used
    icon = CustomIcon(
        "https://www.ebi.ac.uk/pdbe/pdbe-kb/static/icon/favicon-32x32.png",
        icon_size=(22, 22),
        icon_anchor=(11, 11),
        popup_anchor=(0, 0)
    )
    folium.Marker(
        location=[lat, lng],
        icon=icon,
        popup=label,
    ).add_to(marker_clusters[country])
# Display the map
pdbekb_map

In [12]:
# Base map. The tiles parameter defines how it looks like. Good options for this use case in my view are:
# "cartodbpositron", "Stamen watercolor", "Stamen toner". More options on the Folium documentation:
# https://python-visualization.github.io/folium/quickstart.html

pdbekb_map = folium.Map(location=[30, 0], zoom_start=2.1, tiles='cartodbpositron')

# Some utility styles, which can be as fancy as you like, really
# The colour codes used below are from http://colorbrewer2.org
# I copied them here purely for ease of access
# greens: ['#e5f5e0','#a1d99b','#31a354']
# blues: ['#deebf7','#9ecae1','#3182bd']

style_grey = lambda x: {
    'fillColor': '#cccccc',
    'color': "#aaaaaa"
}
style_green = lambda x: {
    'fillColor': '#e5f5e0',
    'color': "#a1d99b"
}
style_blue = lambda x: {
    'fillColor': '#deebf7',
    'color': "#9ecae1"
}

# Go over the countries of the world and check if PDBe-KB has partners in them
# Add their outlines to the map, skip others
for feature in countries_geo['features']:  
    if feature["properties"]["ADMIN"] in partners["Country"].values:
        folium.GeoJson(
            feature,
            style_function=style_green,
            name='geojson'
        ).add_to(pdbekb_map)    

# Create a cluster of markers for ech country. This looks better than each marker separately at low zoom
# At high zoom, the clusters split into individual labels
marker_clusters = {}
for country in set(partners.Country.values):
    marker_clusters[country] = plugins.MarkerCluster().add_to(pdbekb_map)

# Create markers and labels and add them to the cluster for the correct country
# They can also be aded to the map directly, but then will not be aggregated
for lat, lng, resource, url, country in zip(partners.Latitude, 
                                            partners.Longitude, 
                                            partners.index, 
                                            partners.URL,
                                            partners.Country
                                           ):
    label = f"<a href={url} target=_blank>{resource}</a>"
    folium.Marker(
        location=[lat, lng],
        icon=folium.Icon(
            color="green"
        ),
        popup=label,
    ).add_to(marker_clusters[country])
# Display the map
pdbekb_map